In [87]:
import pandas as pd
from ast import literal_eval
import nltk
import re
from gensim.models import Word2Vec
from sklearn.manifold import TSNE
import numpy as np
import matplotlib.pyplot as plt
from collections import Counter

In [88]:
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report, f1_score
from sklearn.model_selection import train_test_split
import metrics

from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Viktor\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [89]:
# scipy is needed in the version 1.10.1
#pip freeze | findstr scipy

# Load Datasets

We load the preprocessed datasets. Make sure to run the previous notebooks first, so the files are present.

## media

In [90]:
df_media = pd.read_csv('../data/cleantech-media.csv', converters={"token_content": literal_eval}, parse_dates=['date'])
df_media.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9588 entries, 0 to 9587
Data columns (total 7 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   title          9588 non-null   object        
 1   date           9588 non-null   datetime64[ns]
 2   author         31 non-null     object        
 3   content        9588 non-null   object        
 4   domain         9588 non-null   object        
 5   url            9588 non-null   object        
 6   token_content  9588 non-null   object        
dtypes: datetime64[ns](1), object(6)
memory usage: 524.5+ KB


In [91]:
df_media.head(5)

title       date author  \
0   Qatar to Slash Emissions as LNG Expansion Advances 2021-01-13    NaN   
1                 India Launches Its First 700 MW PHWR 2021-01-15    NaN   
2                New Chapter for US-China Energy Trade 2021-01-20    NaN   
3  Japan: Slow Restarts Cast Doubt on 2030 Energy Plan 2021-01-22    NaN   
4       NYC Pension Funds to Divest Fossil Fuel Shares 2021-01-25    NaN   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

## patents

In [92]:
df_patents = pd.read_csv('../data/google_patents.csv', converters={"token_content": literal_eval}, parse_dates=['publication_date'])
df_patents.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13199 entries, 0 to 13198
Data columns (total 9 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   publication_number  13199 non-null  object        
 1   application_number  13199 non-null  object        
 2   country_code        13199 non-null  object        
 3   publication_date    13199 non-null  datetime64[ns]
 4   inventor            13199 non-null  object        
 5   title               13199 non-null  object        
 6   abstract            13199 non-null  object        
 7   abstract_lang       13199 non-null  object        
 8   token_content       13199 non-null  object        
dtypes: datetime64[ns](1), object(8)
memory usage: 928.2+ KB


In [93]:
df_patents.head()

publication_number application_number country_code publication_date  \
0   US-2022239235-A1  US-202217717397-A           US       2022-07-28   
1   US-2022239251-A1  US-202217580956-A           US       2022-07-28   
2     US-11396827-B2  US-202117606042-A           US       2022-07-26   
3     CN-114772674-A  CN-202210500131-A           CN       2022-07-22   
4     CN-217026795-U  CN-202220668705-U           CN       2022-07-22   

  inventor  \
0       []   
1       []   
2       []   
3       []   
4       []   

                                                                                                                                title  \
0                                                                                 Adaptable DC-AC Inverter Drive System and Operation   
1                    System for providing the energy from a single contiguous solar energy structure to at least two different meters   
2  Control method for optimizing solar-to-power efficiency of solar-aided coal-fired power system under off-design working conditions   
3                           Low-carbon running saline wastewater treatment system and method applying solar energy and loop heat pipe   
4                                                                  Water ecological remediation device convenient to height-adjusting   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   abstract  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               

# Pre-processing

Mostly taken form previous notebook, but without lemmatizing/stemming.

In [94]:
from nltk.corpus import stopwords
nltk.download('stopwords')

stop_words_nltk = stopwords.words('english')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Viktor\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [95]:
def preprocess_text(text):

    # Keep only letters and spaces
    text = re.sub(r'[^a-zA-Z\s]+', '', text)

    # tokenize the text
    re_tokens = re.findall('[\w]+', text)

    # remove stopwords
    filtered_stopwords = []
    for word in re_tokens:
        if word.lower() not in stop_words_nltk:
            filtered_stopwords.append(word.lower())
        else:
            pass

    return filtered_stopwords

preprocess_text('This, my Friend, is a % test. Have I passed?')

['friend', 'test', 'passed']

In [96]:
#%%timeit 
media_tokens = df_media['content'].apply(lambda x: preprocess_text(x))

In [97]:
media_tokens[:10]

0                                                   [qatar, petroleum, qp, targeting, aggressive, cuts, greenhouse, gas, emissions, prepares, launch, phase, planned, million, ton, per, year, lng, expansion, latest, sustainability, report, published, wednesday, qp, said, goals, include, reducing, emissions, intensity, qatars, lng, facilities, upstream, facilities, least, company, also, aiming, reduce, gas, flaring, intensity, across, upstream, facilities, raised, carbon, capture, storage, ambitions, million, tonsyr, million, tonsyr, million, tonsyr, carbon, capture, goal, come, million, tonyr, phase, lng, expansion, also, known, north, field, east, project, million, tonsyr, come, phase, known, north, field, south, project, raise, qatars, lng, capacity, million, tonsyr, qatar, currently, lng, production, capacity, around, million, tonsyr, eyeing, phased, expansion, million, ...]
1                                  [nuclear, power, corp, india, ltd, npcil, synchronized, kakrapar, western, 

In [98]:
# number of words
len([word for sublist in media_tokens for word in sublist])

4314610

In [99]:
# number of unique words
len(set([word for sublist in media_tokens for word in sublist]))

87078

In [100]:
#%%timeit 
patent_tokens = df_patents['abstract'].apply(lambda x: preprocess_text(x))

In [101]:
patent_tokens[:10]

0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             [disclosed, adaptable, dcac, inverter, system, operation, system, includes, multiple, dc, input, sources, input, provide, stable, operation, various, conditions, dc, input, sources, may, added, system, removed, system, without, impacting, functionality, system, disclosed, system, suited, solar, energy, harvesting, gridconnected, offgrid, modes, operation]
1                                                   

In [102]:
# number of words
len([word for sublist in patent_tokens for word in sublist])

1534180

In [103]:
# number of unique words
len(set([word for sublist in patent_tokens for word in sublist]))

20002

# Generate Text Embeddings

## Train baseline model with default params

## Create a tagged document of the media_tokens

In [104]:
tagged_data_media = [TaggedDocument(words=doc, tags=[str(i)]) for i, doc in enumerate(media_tokens)]
tagged_data_media

[TaggedDocument(words=['qatar', 'petroleum', 'qp', 'targeting', 'aggressive', 'cuts', 'greenhouse', 'gas', 'emissions', 'prepares', 'launch', 'phase', 'planned', 'million', 'ton', 'per', 'year', 'lng', 'expansion', 'latest', 'sustainability', 'report', 'published', 'wednesday', 'qp', 'said', 'goals', 'include', 'reducing', 'emissions', 'intensity', 'qatars', 'lng', 'facilities', 'upstream', 'facilities', 'least', 'company', 'also', 'aiming', 'reduce', 'gas', 'flaring', 'intensity', 'across', 'upstream', 'facilities', 'raised', 'carbon', 'capture', 'storage', 'ambitions', 'million', 'tonsyr', 'million', 'tonsyr', 'million', 'tonsyr', 'carbon', 'capture', 'goal', 'come', 'million', 'tonyr', 'phase', 'lng', 'expansion', 'also', 'known', 'north', 'field', 'east', 'project', 'million', 'tonsyr', 'come', 'phase', 'known', 'north', 'field', 'south', 'project', 'raise', 'qatars', 'lng', 'capacity', 'million', 'tonsyr', 'qatar', 'currently', 'lng', 'production', 'capacity', 'around', 'million',

In [105]:
pd.set_option('display.max_colwidth', None)
print(tagged_data_media[2:4])

[TaggedDocument(words=['new', 'us', 'president', 'joe', 'biden', 'took', 'office', 'week', 'uschina', 'relationship', 'worst', 'decades', 'energy', 'come', 'play', 'bigger', 'role', 'relationship', 'ever', 'rising', 'chinese', 'imports', 'us', 'oil', 'lng', 'could', 'serve', 'foundation', 'fresh', 'discussions', 'trade', 'one', 'areas', 'uschina', 'communications', 'completely', 'broken', 'tackling', 'climate', 'change', 'priority', 'biden', 'unlike', 'predecessor', 'donald', 'trump', 'may', 'offer', 'easiest', 'biggest', 'opportunity', 'cooperation', 'two', 'powers', 'due', 'bipartisan', 'perception', 'china', 'economic', 'geopolitical', 'technological', 'rise', 'poses', 'existential', 'threat', 'us', 'biden', 'administration', 'unlikely', 'soften', 'tone', 'beijing', 'trump', 'demanded', 'bigger', 'purchases', 'us', 'energy', 'products', 'china', 'part', 'phase', 'trade', 'deal', 'would', 'lift', 'us', 'tariffs', 'chinese', 'products', 'biden', 'november', 'us', 'presidential', 'elec

In [106]:
# Split the tagged dataset into a train and a test dataset
train_data_media, test_data_media = train_test_split(tagged_data_media, test_size=0.3, random_state=42)

In [107]:
# Initialize and train the Doc2Vec model on the train data
model_media = Doc2Vec(vector_size=100, window=5, min_count=1, workers=4, epochs=20)
model_media.build_vocab(train_data_media)
model_media.train(train_data_media, total_examples=model_media.corpus_count, epochs=model_media.epochs)

In [108]:
# Check vocabulary size
model_media.corpus_total_words


3019390

In [109]:
model.wv.most_similar('oil')

[('atuabocote', 0.6196202635765076),
 ('hydrofluorite', 0.614647388458252),
 ('natural', 0.565683901309967),
 ('minersoil', 0.5592196583747864),
 ('shoehorned', 0.5583204627037048),
 ('oodles', 0.5543128848075867),
 ('daman', 0.5532512068748474),
 ('noncondensable', 0.5436508059501648),
 ('antioil', 0.5355721712112427),
 ('dieselburner', 0.5353668332099915)]

In [110]:
# Building the vector feature for the classifier:
def vector_for_learning(model, documents):
    sentences = documents
    targets, feature_vectors = zip(*[(doc.tags[0], model.infer_vector(doc.words, alpha=0.025, epochs=20)) for doc in sentences])
    return targets, feature_vectors

In [111]:
y_train, X_train = vector_for_learning(model_media, train_data_media)
y_test, X_test = vector_for_learning(model_media, test_data_media)

In [112]:
# Checkout our best performing model: lg. Can we improve it?
model_lg_media = LogisticRegression()
model_lg_media.fit(X_train, y_train)

LogisticRegression()

In [113]:
# Compare text vectorization with lg
#print(model_lg.score(testFeatureSet, test_labels))
print(model_lg_media.score(X_test, y_test))

0.0


In [114]:
predicted = model_lg_media.predict(X_test)
print(classification_report(y_test, predicted))

              precision    recall  f1-score   support

           0       0.00      0.00      0.00       1.0
          10       0.00      0.00      0.00       1.0
         100       0.00      0.00      0.00       1.0
        1000       0.00      0.00      0.00       0.0
        1002       0.00      0.00      0.00       1.0
        1003       0.00      0.00      0.00       0.0
        1005       0.00      0.00      0.00       1.0
        1009       0.00      0.00      0.00       1.0
         101       0.00      0.00      0.00       1.0
        1010       0.00      0.00      0.00       1.0
        1013       0.00      0.00      0.00       0.0
        1016       0.00      0.00      0.00       0.0
        1017       0.00      0.00      0.00       1.0
        1018       0.00      0.00      0.00       1.0
         102       0.00      0.00      0.00       1.0
        1020       0.00      0.00      0.00       1.0
        1022       0.00      0.00      0.00       1.0
        1025       0.00    

c:\Users\Viktor\switchdrive\Master Data Science\Semester 4\CLT\Project\clt-cleantech-project\.venv\lib\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Viktor\switchdrive\Master Data Science\Semester 4\CLT\Project\clt-cleantech-project\.venv\lib\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Viktor\switchdrive\Master Data Science\Semester 4\CLT\Project\clt-cleantech-project\.venv\lib\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set

## Finetune the model

In [ ]:
# Update vocabulary
model.build_vocab(test_data_media, update=True)

# Fine-tune the Doc2Vec model
model.train(test_data_media, total_examples=model.corpus_count, epochs=model.epochs)

# Evaluate performance
# You can evaluate the performance of the fine-tuned model on specific tasks or downstream applications.



## Create a tagged document of the patent_tokens

In [116]:
tagged_data_patent = [TaggedDocument(words=doc, tags=[str(i)]) for i, doc in enumerate(patent_tokens)]

In [117]:
# Split the tagged dataset into a train and a test dataset
train_data_patent, test_data_patent = train_test_split(tagged_data_patent, test_size=0.3, random_state=42)

In [118]:
# Initialize and train the Doc2Vec model on the train data
model_patent = Doc2Vec(vector_size=100, window=5, min_count=1, workers=4, epochs=20)
model_patent.build_vocab(train_data_patent)
model_patent.train(train_data_patent, total_examples=model.corpus_count, epochs=model.epochs)

In [119]:
# Check vocabulary size
model_patent.corpus_total_words


1072257

In [120]:
y_train_patent, X_train_patent = vector_for_learning(model_patent, train_data_media)
y_test_patent, X_test_patent = vector_for_learning(model_patent, test_data_media)

In [121]:
# Checkout our best performing model: lg. Can we improve it?
model_lg_patent = LogisticRegression()
model_lg_patent.fit(X_train, y_train)

LogisticRegression()

In [122]:
# Compare text vectorization with lg
print(model_lg_patent.score(X_test_patent, y_test_patent))
print(model_lg_media.score(X_test, y_test))

0.0
0.0


In [123]:
predicted_patent = model_lg_media.predict(X_test_patent)
print(classification_report(y_test_patent, predicted_patent))

              precision    recall  f1-score   support

           0       0.00      0.00      0.00       1.0
          10       0.00      0.00      0.00       1.0
         100       0.00      0.00      0.00       1.0
        1002       0.00      0.00      0.00       1.0
        1005       0.00      0.00      0.00       1.0
        1009       0.00      0.00      0.00       1.0
         101       0.00      0.00      0.00       1.0
        1010       0.00      0.00      0.00       1.0
        1013       0.00      0.00      0.00       0.0
        1017       0.00      0.00      0.00       1.0
        1018       0.00      0.00      0.00       1.0
         102       0.00      0.00      0.00       1.0
        1020       0.00      0.00      0.00       1.0
        1022       0.00      0.00      0.00       1.0
        1025       0.00      0.00      0.00       1.0
        1027       0.00      0.00      0.00       1.0
         103       0.00      0.00      0.00       1.0
        1034       0.00    

c:\Users\Viktor\switchdrive\Master Data Science\Semester 4\CLT\Project\clt-cleantech-project\.venv\lib\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Viktor\switchdrive\Master Data Science\Semester 4\CLT\Project\clt-cleantech-project\.venv\lib\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Viktor\switchdrive\Master Data Science\Semester 4\CLT\Project\clt-cleantech-project\.venv\lib\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set